In [16]:
import pandas as pd
import wandb

api = wandb.Api()

# Project is specified by <entity/project-name>
runs = api.runs("jameswburton18/OrientalMuesumImage")

summary_list, config_list, name_list = [], [], []
for run in runs:
    # .summary contains the output keys/values for metrics like accuracy.
    #  We call ._json_dict to omit large files
    summary_list.append(run.summary._json_dict)

    # .config contains the hyperparameters.
    #  We remove special values that start with _.
    config_list.append({k: v for k, v in run.config.items() if not k.startswith("_")})

    # .name is the human-readable name of the run.
    name_list.append(run.name)

runs_df = pd.DataFrame({"summary": summary_list, "config": config_list, "name": name_list})

In [17]:
runs_df

summary  \
0    {'test_avg_plus_3Dx4_w0.0/f1_micro': 0.5605381...   
1    {'test_steps_per_second': 0.804, 'test_avg_plu...   
2    {'test_avg_plus_3Dx4_w0.75/f1_weighted': 0.537...   
3    {'eval/accuracy': 0.4373990306946688, 'test_av...   
4    {'eval/accuracy': 0.33037156704361875, 'eval/f...   
..                                                 ...   
303  {'test_precision_macro': 0.1243382563150882, '...   
304  {'_runtime': 4879.275132894516, 'eval/accuracy...   
305  {'eval/recall_macro': 0.6267291174075081, 'tes...   
306  {'eval/accuracy': 0.11090675004598124, 'train/...   
307  {'eval/samples_per_second': 116.434, 'train/tr...   

                                                config                name  
0    {'my_args/lr': 5e-05, 'my_args/fp16': True, 'm...     valiant-sky-376  
1    {'my_args/lr': 5e-05, 'my_args/fp16': True, 'm...       sweet-fog-375  
2    {'my_args/lr': 5e-05, 'my_args/fp16': False, '...     lively-lion-374  
3    {'bf16': False, 'fp16': False, 'fsdp': [], 'se...     peachy-tree-373  
4    {'bf16': False, 'fp16': True, 'fsdp': [], 'see...    upbeat-sound-372  
..                                                 ...                 ...  
303  {'bf16': False, 'fp16': False, 'fsdp': [], 'se...     crimson-surf-33  
304  {'bf16': False, 'fp16': False, 'fsdp': [], 'se...  eternal-silence-32  
305  {'bf16': False, 'fp16': False, 'fsdp': [], 'se...       leafy-dawn-31  
306  {'bf16': False, 'fp16': False, 'fsdp': [], 'se...    peach-morning-30  
307  {'bf16': False, 'fp16': False, 'fsdp': [], 'se...  generous-breeze-29  

[308 rows x 3 columns]

In [18]:
ds_to_technique = {
    "james-burton/OrientalMuseum-3Dwhite-1frame": "white+3Dx1",
    "james-burton/OrientalMuseum-3Dwhite": "white+3Dx4",
    "james-burton/OrientalMuseum-white": "white",
    # "james-burton/OrientalMuseum": "normal",
}


metrics = [
    "accuracy",
    "top3_accuracy",
    "top5_accuracy",
    "top10_accuracy",
    "f1_weighted",
    "precision_weighted",
    "recall_weighted",
    "f1_macro",
    "precision_macro",
    "recall_macro",
    "f1_micro",
    "precision_micro",
    "recall_micro",
    # "avg_images_per_item",
]


def get_pretrained(x):
    if "pretrn" in x:
        return "Yes"
    else:
        return "No"


def get_filtered_df(
    runs_df,
    exp_type,
    exclude_classes_less_than_x_items=None,
    label_col=None,
    dataset=None,
    metrics=metrics,
):
    new_df = pd.DataFrame()
    new_df["run_num"] = runs_df["name"].apply(lambda x: int(x.split("-")[-1]))
    new_df["config"] = runs_df["config"].apply(lambda x: x.get("my_args/config", None))
    new_df["exclude classes less than x items"] = runs_df["config"].apply(
        lambda x: x.get("my_args/lower_lim", None)
    )
    new_df["label_col"] = runs_df["config"].apply(lambda x: x.get("my_args/label_col", None))
    new_df["BM pretrain"] = new_df["config"].map(get_pretrained)
    new_df["Train data"] = runs_df["config"].apply(lambda x: x.get("my_args/dataset", None))
    new_df["Train data"] = new_df["Train data"].apply(lambda x: ds_to_technique.get(x, None))
    for metric in metrics:
        if exp_type == "test_" and metric in ["avg_images_per_item"]:
            continue
        new_df[metric] = runs_df["summary"].apply(lambda x: x.get(exp_type + metric, None))
        # set to 2 decimal places
        new_df[metric] = new_df[metric].apply(lambda x: round(x, 3) if x is not None else None)
    new_df = new_df.dropna()
    max_run_nums = new_df.groupby("config")["run_num"].idxmax()
    filtered_df = new_df.loc[max_run_nums]
    if exclude_classes_less_than_x_items is not None:
        filtered_df = filtered_df[
            filtered_df["exclude classes less than x items"] == exclude_classes_less_than_x_items
        ]
        filtered_df = filtered_df.drop(columns=["exclude classes less than x items"])
    if dataset is not None:
        filtered_df = filtered_df[filtered_df["Train data"] == dataset]
        filtered_df = filtered_df.drop(columns=["Train data"])
    if label_col is not None:
        filtered_df = filtered_df[filtered_df["label_col"] == label_col]
        filtered_df = filtered_df.drop(columns=["label_col"])
    filtered_df.drop(columns=["run_num"], inplace=True)
    filtered_df.drop(
        columns=[
            "f1_macro",
            "precision_macro",
            "recall_macro",
            "f1_micro",
            "precision_micro",
            "recall_micro",
        ],
        inplace=True,
    )
    filtered_df.rename(
        columns={
            "accuracy": "Acc.",
            "top3_accuracy": "Top 3 Acc.",
            "top5_accuracy": "Top 5 Acc.",
            "top10_accuracy": "Top 10 Acc.",
            "f1_weighted": "F1",
            "precision_weighted": "Precision",
            "recall_weighted": "Recall",
        },
        inplace=True,
    )
    return filtered_df

In [19]:
exp_types = (
    [
        # "test_",  # Normal
        "test_avg/",  # Averaged over each item
    ]
    + [f"test_avg_max{i}/" for i in range(1, 6)]  # Averaged over each item, max i images per item
    + [
        f"test_avg_plus_3Dx4_w{w}/" for w in [0.0, 0.25, 0.5, 0.75, 1.0]
    ]  # Averaged over each item, plus weighted 3D predictions
    + [
        f"test_avg_max1_plus_3Dx4_w{w}/" for w in [0.0, 0.25, 0.5, 0.75, 1.0]
    ]  # Averaged over each item, max 1 images per item, plus weighted 3D predictions
)

## Predict object
Given an image of an object we have seen before, but from a different angle, can we predict what that object is?

In [20]:
get_filtered_df(runs_df, "test_", exclude_classes_less_than_x_items=6, label_col="obj_num")

config BM pretrain  Train data   Acc.  \
146            om6-3Dwhite-1frame_num          No  white+3Dx1  0.820   
48   om6-3Dwhite-1frame_num_bm-pretrn         Yes  white+3Dx1  0.801   
217                   om6-3Dwhite_num          No  white+3Dx4  0.826   
51          om6-3Dwhite_num_bm-pretrn         Yes  white+3Dx4  0.822   
239                     om6-white_num          No       white  0.828   
54            om6-white_num_bm-pretrn         Yes       white  0.819   

     Top 3 Acc.  Top 5 Acc.  Top 10 Acc.     F1  Precision  Recall  
146       0.893       0.914        0.936  0.794      0.803   0.820  
48        0.880       0.900        0.925  0.774      0.787   0.801  
217       0.898       0.918        0.934  0.800      0.811   0.826  
51        0.884       0.911        0.937  0.798      0.812   0.822  
239       0.898       0.918        0.941  0.804      0.813   0.828  
54        0.881       0.901        0.925  0.791      0.800   0.819

## Predict material
Given one or more images from an object we have never seen before, can we predict what that object is made from?

In [21]:
for max1 in ["_max1", ""]:
    for x in [3, 4, 5, 6]:

        material_x = get_filtered_df(
            runs_df, f"test_avg{max1}/", exclude_classes_less_than_x_items=x, label_col="material"
        )
        material_x["Test time method"] = "avg"
        material_x_plus3Ds = []
        for w in [0.75]:  # [0.25, 0.5, 0.75]:
            df = get_filtered_df(
                runs_df,
                f"test_avg{max1}_plus_3Dx4_w{w}/",
                exclude_classes_less_than_x_items=x,
                label_col="material",
            )
            # df["Test time method"] = f"average_w{w}_plus_3D_w{1-w}"
            df["Test time method"] = f"avg+3D"
            material_x_plus3Ds.append(df)

        material_x_plus3Ds = pd.concat([material_x, pd.concat(material_x_plus3Ds)])

        cols = ["BM pretrain", "Train data", "Test time method"]
        other_cols = [col for col in material_x_plus3Ds.columns if col not in cols]
        material_x_plus3Ds = material_x_plus3Ds[cols + other_cols]

        material_x_plus3Ds.sort_values(
            by=["BM pretrain", "Train data", "Test time method"], inplace=True
        )

        # # Assuming your DataFrame is named 'df'
        # # Create a copy to avoid modifying the original DataFrame
        df_new = material_x_plus3Ds.copy()

        # For column 'BM Pretrain'
        df_new["BM pretrain"] = df_new["BM pretrain"].where(
            df_new["BM pretrain"] != df_new["BM pretrain"].shift(1), ""
        )

        # For column 'Train data'
        df_new["Train data"] = df_new["Train data"].where(
            df_new["Train data"] != df_new["Train data"].shift(1), ""
        )
        df_new.drop(columns=["config"], inplace=True)
        df_new.to_csv(f"material_min{x}{max1}.csv", index=False)
df_new

BM pretrain  Train data Test time method   Acc.  Top 3 Acc.  Top 5 Acc.  \
117          No       white              avg  0.632       0.817       0.878   
85                                    avg+3D  0.632       0.811       0.869   
114              white+3Dx1              avg  0.615       0.817       0.878   
81                                    avg+3D  0.620       0.818       0.880   
115              white+3Dx4              avg  0.628       0.819       0.879   
83                                    avg+3D  0.624       0.819       0.880   
53          Yes       white              avg  0.641       0.824       0.886   
26                                    avg+3D  0.644       0.834       0.885   
47               white+3Dx1              avg  0.622       0.818       0.880   
21                                    avg+3D  0.617       0.813       0.879   
50               white+3Dx4              avg  0.640       0.824       0.879   
23                                    avg+3D  0.648       0.827       0.883   

     Top 10 Acc.     F1  Precision  Recall  
117        0.927  0.606      0.598   0.632  
85         0.924  0.602      0.593   0.632  
114        0.929  0.593      0.617   0.615  
81         0.928  0.597      0.623   0.620  
115        0.933  0.604      0.611   0.628  
83         0.933  0.597      0.598   0.624  
53         0.934  0.614      0.610   0.641  
26         0.938  0.617      0.618   0.644  
47         0.935  0.593      0.590   0.622  
21         0.932  0.586      0.584   0.617  
50         0.936  0.615      0.615   0.640  
23         0.940  0.622      0.622   0.648

### If we have only have one/two/three/four images

In [ ]:
x = 3
material_x = get_filtered_df(
    runs_df, "test_avg_max1/", exclude_classes_less_than_x_items=x, label_col="material"
)
material_x["test_time_technique"] = "average"
material_x_plus3Ds = []
for w in [0.25, 0.5, 0.75]:
    df = get_filtered_df(
        runs_df,
        f"test_avg_max1_plus_3Dx4_w{w}/",
        exclude_classes_less_than_x_items=x,
        label_col="material",
    )
    df["test_time_technique"] = f"average_w{w}_plus_3D_w{1-w}"
    material_x_plus3Ds.append(df)

### If we have only have one/two/three/four images

One

In [8]:
get_filtered_df(
    runs_df, "test_avg_max1/", exclude_classes_less_than_x_items=5, label_col="material"
)

dataset  accuracy  top3_accuracy  top5_accuracy  top10_accuracy  \
43   white3D-1frame     0.604          0.774          0.840           0.915   
45  white3D-4frames     0.593          0.792          0.849           0.911   
47            white     0.565          0.742          0.813           0.887   
49           normal     0.683          0.814          0.874           0.926   

    f1_weighted  precision_weighted  recall_weighted  f1_macro  \
43        0.580               0.581            0.604     0.321   
45        0.565               0.563            0.593     0.298   
47        0.536               0.569            0.565     0.328   
49        0.668               0.668            0.683     0.385   

    precision_macro  recall_macro  f1_micro  precision_micro  recall_micro  \
43            0.345         0.326     0.604            0.604         0.604   
45            0.312         0.312     0.593            0.593         0.593   
47            0.343         0.349     0.565            0.565         0.565   
49            0.406         0.396     0.683            0.683         0.683   

    avg_images_per_item  
43                  1.0  
45                  1.0  
47                  1.0  
49                  1.0

Two

In [9]:
get_filtered_df(
    runs_df, "test_avg_max2/", exclude_classes_less_than_x_items=5, label_col="material"
)

dataset  accuracy  top3_accuracy  top5_accuracy  top10_accuracy  \
43   white3D-1frame     0.630          0.798          0.862           0.919   
45  white3D-4frames     0.624          0.811          0.865           0.921   
47            white     0.597          0.767          0.835           0.906   
49           normal     0.707          0.835          0.892           0.940   

    f1_weighted  precision_weighted  recall_weighted  f1_macro  \
43        0.602               0.603            0.630     0.337   
45        0.593               0.597            0.624     0.320   
47        0.563               0.589            0.597     0.359   
49        0.692               0.696            0.707     0.428   

    precision_macro  recall_macro  f1_micro  precision_micro  recall_micro  \
43            0.364         0.340     0.630            0.630         0.630   
45            0.347         0.333     0.624            0.624         0.624   
47            0.379         0.381     0.597            0.597         0.597   
49            0.464         0.436     0.707            0.707         0.707   

    avg_images_per_item  
43                1.534  
45                1.534  
47                1.534  
49                1.534

Three

In [10]:
get_filtered_df(
    runs_df, "test_avg_max3/", exclude_classes_less_than_x_items=5, label_col="material"
)

dataset  accuracy  top3_accuracy  top5_accuracy  top10_accuracy  \
43   white3D-1frame     0.629          0.803          0.866           0.922   
45  white3D-4frames     0.631          0.814          0.870           0.923   
47            white     0.603          0.771          0.839           0.910   
49           normal     0.707          0.836          0.892           0.944   

    f1_weighted  precision_weighted  recall_weighted  f1_macro  \
43        0.601               0.603            0.629     0.337   
45        0.598               0.602            0.631     0.314   
47        0.568               0.610            0.603     0.365   
49        0.691               0.694            0.707     0.428   

    precision_macro  recall_macro  f1_micro  precision_micro  recall_micro  \
43            0.362         0.341     0.629            0.629         0.629   
45            0.343         0.323     0.631            0.631         0.631   
47            0.380         0.385     0.603            0.603         0.603   
49            0.461         0.439     0.707            0.707         0.707   

    avg_images_per_item  
43                1.838  
45                1.838  
47                1.838  
49                1.838

Four

In [11]:
get_filtered_df(
    runs_df, "test_avg_max4/", exclude_classes_less_than_x_items=5, label_col="material"
)

dataset  accuracy  top3_accuracy  top5_accuracy  top10_accuracy  \
43   white3D-1frame     0.632          0.803          0.868           0.924   
45  white3D-4frames     0.632          0.812          0.872           0.921   
47            white     0.603          0.776          0.840           0.909   
49           normal     0.706          0.840          0.892           0.946   

    f1_weighted  precision_weighted  recall_weighted  f1_macro  \
43        0.604               0.606            0.632     0.339   
45        0.600               0.603            0.632     0.319   
47        0.568               0.604            0.603     0.369   
49        0.691               0.694            0.706     0.424   

    precision_macro  recall_macro  f1_micro  precision_micro  recall_micro  \
43            0.366         0.342     0.632            0.632         0.632   
45            0.347         0.324     0.632            0.632         0.632   
47            0.386         0.389     0.603            0.603         0.603   
49            0.455         0.436     0.706            0.706         0.706   

    avg_images_per_item  
43                2.083  
45                2.083  
47                2.083  
49                2.083

### If we have only have one images, but we augment at test time with 4 generated 3D views

One

In [12]:
# df = get_filtered_df(
#     runs_df, "test_avg_max1/", exclude_classes_less_than_x_items=5, label_col="material"
# )
# df["genuine_img_w"] = "none"

df_25 = get_filtered_df(
    runs_df,
    "test_avg_max1_plus_3Dx4_w0.25/",
    exclude_classes_less_than_x_items=5,
    label_col="material",
)
df_25["genuine_img_w"] = 0.25
df_50 = get_filtered_df(
    runs_df,
    "test_avg_max1_plus_3Dx4_w0.5/",
    exclude_classes_less_than_x_items=5,
    label_col="material",
)
df_50["genuine_img_w"] = 0.5
df_75 = get_filtered_df(
    runs_df,
    "test_avg_max1_plus_3Dx4_w0.75/",
    exclude_classes_less_than_x_items=5,
    label_col="material",
)
df_75["genuine_img_w"] = 0.75
df_1 = get_filtered_df(
    runs_df,
    "test_avg_max1_plus_3Dx4_w1.0/",
    exclude_classes_less_than_x_items=5,
    label_col="material",
)
df_1["genuine_img_w"] = 1.0

df = pd.concat([df_25, df_50, df_75, df_1])

# put the genuine_img_w column first
cols = df.columns.tolist()
cols = cols[-1:] + cols[:-1]
df = df[cols]

In [13]:
df[df["dataset"] != "normal"].sort_values("accuracy", ascending=False)

genuine_img_w          dataset  accuracy  top3_accuracy  top5_accuracy  \
9            1.00   white3D-1frame     0.603          0.775          0.840   
9            0.75   white3D-1frame     0.599          0.777          0.846   
11           0.50  white3D-4frames     0.595          0.787          0.851   
11           1.00  white3D-4frames     0.593          0.792          0.849   
11           0.75  white3D-4frames     0.591          0.790          0.850   
9            0.50   white3D-1frame     0.587          0.771          0.850   
11           0.25  white3D-4frames     0.581          0.769          0.845   
13           0.75            white     0.568          0.734          0.822   
13           1.00            white     0.565          0.742          0.813   
9            0.25   white3D-1frame     0.564          0.757          0.837   
13           0.50            white     0.545          0.726          0.815   
13           0.25            white     0.460          0.664          0.761   

    top10_accuracy  f1_weighted  precision_weighted  recall_weighted  \
9            0.915        0.579               0.580            0.603   
9            0.919        0.573               0.574            0.599   
11           0.911        0.567               0.570            0.595   
11           0.911        0.565               0.563            0.593   
11           0.917        0.562               0.567            0.591   
9            0.917        0.556               0.562            0.587   
11           0.913        0.553               0.560            0.581   
13           0.899        0.532               0.576            0.568   
13           0.887        0.536               0.569            0.565   
9            0.911        0.529               0.543            0.564   
13           0.900        0.504               0.560            0.545   
13           0.866        0.427               0.503            0.460   

    f1_macro  precision_macro  recall_macro  f1_micro  precision_micro  \
9      0.320            0.345         0.326     0.603            0.603   
9      0.305            0.328         0.308     0.599            0.599   
11     0.296            0.327         0.303     0.595            0.595   
11     0.298            0.312         0.312     0.593            0.593   
11     0.287            0.316         0.299     0.591            0.591   
9      0.287            0.313         0.289     0.587            0.587   
11     0.274            0.299         0.285     0.581            0.581   
13     0.319            0.354         0.333     0.568            0.568   
13     0.330            0.345         0.350     0.565            0.565   
9      0.262            0.292         0.269     0.564            0.564   
13     0.275            0.325         0.285     0.545            0.545   
13     0.199            0.269         0.206     0.460            0.460   

    recall_micro  avg_images_per_item  
9          0.603                  1.0  
9          0.599                  1.0  
11         0.595                  1.0  
11         0.593                  1.0  
11         0.591                  1.0  
9          0.587                  1.0  
11         0.581                  1.0  
13         0.568                  1.0  
13         0.565                  1.0  
9          0.564                  1.0  
13         0.545                  1.0  
13         0.460                  1.0

## Predict category
Given one or more images from an object we have never seen before, can we predict what category that object is in?

In [12]:
get_filtered_df(runs_df, "test_avg/", exclude_classes_less_than_x_items=5, label_col="object_name")

config BM pretrain  Train data   Acc.  \
117            om5-3Dwhite-1frame_name          No  white+3Dx1  0.586   
52   om5-3Dwhite-1frame_name_bm-pretrn         Yes  white+3Dx1  0.592   
119                   om5-3Dwhite_name          No  white+3Dx4  0.601   
55          om5-3Dwhite_name_bm-pretrn         Yes  white+3Dx4  0.584   
121                     om5-white_name          No       white  0.618   
58            om5-white_name_bm-pretrn         Yes       white  0.600   

     Top 3 Acc.  Top 5 Acc.  Top 10 Acc.     F1  Precision  Recall  
117       0.743       0.811        0.875  0.546      0.539   0.586  
52        0.757       0.814        0.871  0.555      0.554   0.592  
119       0.743       0.804        0.874  0.569      0.569   0.601  
55        0.751       0.805        0.870  0.553      0.556   0.584  
121       0.764       0.819        0.891  0.601      0.605   0.618  
58        0.765       0.811        0.871  0.572      0.573   0.600

In [22]:
for max1 in ['_max1', '']:
    for x in [3, 4, 5, 6]:

        category_x = get_filtered_df(
            runs_df, f"test_avg{max1}/", exclude_classes_less_than_x_items=x, label_col="object_name"
        )
        category_x["Test time method"] = "avg"
        category_x_plus3Ds = []
        for w in [0.75]:  # [0.25, 0.5, 0.75]:
            df = get_filtered_df(
                runs_df,
                f"test_avg{max1}_plus_3Dx4_w{w}/",
                exclude_classes_less_than_x_items=x,
                label_col="object_name",
            )
            # df["Test time method"] = f"average_w{w}_plus_3D_w{1-w}"
            df["Test time method"] = f"avg+3D"
            category_x_plus3Ds.append(df)

        category_x_plus3Ds = pd.concat([
            category_x, pd.concat(category_x_plus3Ds)
        ])

        cols = ["BM pretrain", "Train data", "Test time method"]
        other_cols = [col for col in category_x_plus3Ds.columns if col not in cols]
        category_x_plus3Ds = category_x_plus3Ds[cols + other_cols]

        category_x_plus3Ds.sort_values(by=["BM pretrain", "Train data", "Test time method"], inplace=True)

        # # Assuming your DataFrame is named 'df'
        # # Create a copy to avoid modifying the original DataFrame
        df_new = category_x_plus3Ds.copy()

        # For column 'BM Pretrain'
        df_new["BM pretrain"] = df_new["BM pretrain"].where(
            df_new["BM pretrain"] != df_new["BM pretrain"].shift(1), ""
        )

        # For column 'Train data'
        df_new["Train data"] = df_new["Train data"].where(
            df_new["Train data"] != df_new["Train data"].shift(1), ""
        )
        df_new.drop(columns=['config'], inplace=True)
        df_new.to_csv(f"object_name_min{x}{max1}.csv", index=False)
df_new

BM pretrain  Train data Test time method   Acc.  Top 3 Acc.  Top 5 Acc.  \
116          No       white              avg  0.624       0.772       0.831   
84                                    avg+3D  0.613       0.772       0.824   
112              white+3Dx1              avg  0.616       0.765       0.821   
80                                    avg+3D  0.617       0.760       0.827   
113              white+3Dx4              avg  0.600       0.761       0.811   
82                                    avg+3D  0.604       0.759       0.816   
52          Yes       white              avg  0.611       0.772       0.822   
25                                    avg+3D  0.613       0.773       0.829   
46               white+3Dx1              avg  0.616       0.769       0.827   
19                                    avg+3D  0.622       0.768       0.824   
49               white+3Dx4              avg  0.602       0.759       0.823   
22                                    avg+3D  0.609       0.754       0.818   

     Top 10 Acc.     F1  Precision  Recall  
116        0.888  0.609      0.621   0.624  
84         0.886  0.598      0.614   0.613  
112        0.885  0.600      0.607   0.616  
80         0.882  0.600      0.605   0.617  
113        0.882  0.577      0.590   0.600  
82         0.883  0.580      0.593   0.604  
52         0.876  0.582      0.578   0.611  
25         0.876  0.592      0.598   0.613  
46         0.880  0.594      0.602   0.616  
19         0.886  0.606      0.612   0.622  
49         0.880  0.575      0.584   0.602  
22         0.877  0.592      0.608   0.609

### If we have only have one/two/three/four images

One

In [15]:
get_filtered_df(
    runs_df, "test_avg_max1/", exclude_classes_less_than_x_items=5, label_col="object_name"
)

dataset  accuracy  top3_accuracy  top5_accuracy  top10_accuracy  \
42   white3D-1frame     0.551          0.719          0.783           0.857   
44  white3D-4frames     0.562          0.716          0.781           0.853   
46            white     0.578          0.724          0.789           0.875   
48           normal     0.651          0.794          0.846           0.895   

    f1_weighted  precision_weighted  recall_weighted  f1_macro  \
42        0.514               0.507            0.551     0.249   
44        0.533               0.533            0.562     0.286   
46        0.569               0.579            0.578     0.346   
48        0.630               0.634            0.651     0.368   

    precision_macro  recall_macro  f1_micro  precision_micro  recall_micro  \
42            0.263         0.265     0.551            0.551         0.551   
44            0.304         0.301     0.562            0.562         0.562   
46            0.364         0.359     0.578            0.578         0.578   
48            0.395         0.377     0.651            0.651         0.651   

    avg_images_per_item  
42                  1.0  
44                  1.0  
46                  1.0  
48                  1.0

Two

In [16]:
get_filtered_df(
    runs_df, "test_avg_max2/", exclude_classes_less_than_x_items=5, label_col="object_name"
)

dataset  accuracy  top3_accuracy  top5_accuracy  top10_accuracy  \
42   white3D-1frame     0.577          0.738          0.804           0.871   
44  white3D-4frames     0.586          0.738          0.793           0.868   
46            white     0.600          0.749          0.809           0.885   
48           normal     0.679          0.808          0.857           0.906   

    f1_weighted  precision_weighted  recall_weighted  f1_macro  \
42        0.538               0.531            0.577     0.273   
44        0.554               0.552            0.586     0.311   
46        0.585               0.589            0.600     0.362   
48        0.657               0.660            0.679     0.396   

    precision_macro  recall_macro  f1_micro  precision_micro  recall_micro  \
42            0.291         0.290     0.577            0.577         0.577   
44            0.332         0.321     0.586            0.586         0.586   
46            0.371         0.385     0.600            0.600         0.600   
48            0.417         0.410     0.679            0.679         0.679   

    avg_images_per_item  
42                1.504  
44                1.504  
46                1.504  
48                1.504

Three

In [17]:
get_filtered_df(
    runs_df, "test_avg_max3/", exclude_classes_less_than_x_items=5, label_col="object_name"
)

dataset  accuracy  top3_accuracy  top5_accuracy  top10_accuracy  \
42   white3D-1frame     0.584          0.745          0.810           0.874   
44  white3D-4frames     0.595          0.743          0.803           0.871   
46            white     0.613          0.761          0.816           0.889   
48           normal     0.682          0.812          0.860           0.909   

    f1_weighted  precision_weighted  recall_weighted  f1_macro  \
42        0.543               0.534            0.584     0.278   
44        0.563               0.560            0.595     0.322   
46        0.597               0.603            0.613     0.379   
48        0.658               0.661            0.682     0.388   

    precision_macro  recall_macro  f1_micro  precision_micro  recall_micro  \
42            0.295         0.294     0.584            0.584         0.584   
44            0.346         0.330     0.595            0.595         0.595   
46            0.392         0.397     0.613            0.613         0.613   
48            0.415         0.402     0.682            0.682         0.682   

    avg_images_per_item  
42                1.776  
44                1.776  
46                1.776  
48                1.776

Four

In [18]:
get_filtered_df(
    runs_df, "test_avg_max4/", exclude_classes_less_than_x_items=5, label_col="object_name"
)

dataset  accuracy  top3_accuracy  top5_accuracy  top10_accuracy  \
42   white3D-1frame     0.586          0.746          0.809           0.874   
44  white3D-4frames     0.598          0.743          0.803           0.871   
46            white     0.615          0.759          0.815           0.891   
48           normal     0.681          0.813          0.860           0.910   

    f1_weighted  precision_weighted  recall_weighted  f1_macro  \
42        0.545               0.536            0.586     0.284   
44        0.565               0.564            0.598     0.321   
46        0.599               0.605            0.615     0.379   
48        0.656               0.658            0.681     0.388   

    precision_macro  recall_macro  f1_micro  precision_micro  recall_micro  \
42            0.300         0.300     0.586            0.586         0.586   
44            0.348         0.328     0.598            0.598         0.598   
46            0.393         0.399     0.615            0.615         0.615   
48            0.412         0.404     0.681            0.681         0.681   

    avg_images_per_item  
42                2.001  
44                2.001  
46                2.001  
48                2.001

### If we have only have one images, but we augment at test time with 4 generated 3D views

One

In [19]:
# df = get_filtered_df(
#     runs_df, "test_avg_max1/", exclude_classes_less_than_x_items=5, label_col="material"
# )
# df["genuine_img_w"] = "none"

df_25 = get_filtered_df(
    runs_df,
    "test_avg_max1_plus_3Dx4_w0.25/",
    exclude_classes_less_than_x_items=5,
    label_col="object_name",
)
df_25["genuine_img_w"] = 0.25
df_50 = get_filtered_df(
    runs_df,
    "test_avg_max1_plus_3Dx4_w0.5/",
    exclude_classes_less_than_x_items=5,
    label_col="object_name",
)
df_50["genuine_img_w"] = 0.5
df_75 = get_filtered_df(
    runs_df,
    "test_avg_max1_plus_3Dx4_w0.75/",
    exclude_classes_less_than_x_items=5,
    label_col="object_name",
)
df_75["genuine_img_w"] = 0.75
df_1 = get_filtered_df(
    runs_df,
    "test_avg_max1_plus_3Dx4_w1.0/",
    exclude_classes_less_than_x_items=5,
    label_col="object_name",
)
df_1["genuine_img_w"] = 1.0

df = pd.concat([df_25, df_50, df_75, df_1])

# put the genuine_img_w column first
cols = df.columns.tolist()
cols = cols[-1:] + cols[:-1]
df = df[cols]

In [20]:
df[df["dataset"] != "normal"].sort_values("accuracy", ascending=False)

genuine_img_w          dataset  accuracy  top3_accuracy  top5_accuracy  \
12           1.00            white     0.578          0.724          0.789   
12           0.75            white     0.573          0.720          0.785   
10           1.00  white3D-4frames     0.562          0.717          0.781   
10           0.75  white3D-4frames     0.559          0.714          0.785   
10           0.50  white3D-4frames     0.556          0.716          0.780   
8            0.75   white3D-1frame     0.552          0.723          0.785   
8            1.00   white3D-1frame     0.551          0.719          0.783   
8            0.50   white3D-1frame     0.543          0.712          0.775   
10           0.25  white3D-4frames     0.539          0.709          0.769   
12           0.50            white     0.529          0.701          0.772   
8            0.25   white3D-1frame     0.520          0.695          0.760   
12           0.25            white     0.422          0.614          0.692   

    top10_accuracy  f1_weighted  precision_weighted  recall_weighted  \
12           0.875        0.569               0.579            0.578   
12           0.869        0.561               0.573            0.573   
10           0.853        0.533               0.533            0.562   
10           0.851        0.531               0.535            0.559   
10           0.848        0.528               0.531            0.556   
8            0.854        0.513               0.506            0.552   
8            0.857        0.514               0.507            0.551   
8            0.846        0.506               0.503            0.543   
10           0.845        0.510               0.512            0.539   
12           0.850        0.518               0.539            0.529   
8            0.835        0.484               0.484            0.520   
12           0.791        0.408               0.455            0.422   

    f1_macro  precision_macro  recall_macro  f1_micro  precision_micro  \
12     0.346            0.364         0.359     0.578            0.578   
12     0.330            0.357         0.335     0.573            0.573   
10     0.286            0.304         0.301     0.562            0.562   
10     0.288            0.314         0.300     0.559            0.559   
10     0.283            0.310         0.294     0.556            0.556   
8      0.253            0.271         0.266     0.552            0.552   
8      0.249            0.263         0.265     0.551            0.551   
8      0.249            0.270         0.260     0.543            0.543   
10     0.259            0.281         0.271     0.539            0.539   
12     0.292            0.337         0.288     0.529            0.529   
8      0.229            0.251         0.237     0.520            0.520   
12     0.187            0.231         0.188     0.422            0.422   

    recall_micro  avg_images_per_item  
12         0.578                  1.0  
12         0.573                  1.0  
10         0.562                  1.0  
10         0.559                  1.0  
10         0.556                  1.0  
8          0.552                  1.0  
8          0.551                  1.0  
8          0.543                  1.0  
10         0.539                  1.0  
12         0.529                  1.0  
8          0.520                  1.0  
12         0.422                  1.0